In [40]:
import pandas as pd
from datetime import datetime
from datetime import timedelta
from tqdm import tqdm
import warnings
warnings.filterwarnings("ignore")
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense, LSTM,Dropout
import numpy as np
import matplotlib.pyplot as plt

In [41]:
train = pd.read_csv('open/train.csv')

train:test = 7:3 (350:144)로 정해두고 train data로 fit.   
test data중에서 15일만 필요하니까 마지막 15일 가지고 이후 15일 prediction.   
15일로 예측한 하루를 포함해서 또 15일로 예측하는 방식으로. or 총 30일을 가지고 예측하는 방식.    
일단 총 30일을 가지고 예측하는 방식으로. (이미 15일씩 sliding 했어서 30일 가지고 예측하는 방식이 됨)

In [42]:
#train = train[train['종목명']=='아모레퍼시픽']

In [47]:
class LSTM_Prediction:
    def __init__(self):
        pass

    def MinMaxScaler(data):
        numerator = data - np.min(data, 0)
        denominator = np.max(data, 0) - np.min(data, 0)
        return numerator / (denominator + 1e-7)

    def preprocessing(row):
        dfx = row[['시가', '고가', '저가', '거래량', '종가']]
        dfx = LSTM_Prediction.MinMaxScaler(dfx)
        dfy = dfx[['종가']]
        x = dfx.values.tolist()
        y = dfy.values.tolist()

        return x, y, dfy

    def dataset(row):
        x, y, dfy = LSTM_Prediction.preprocessing(row)
        data_x = []
        data_y = []
        window_size = 15
        
        #15일로 -> 하루 예측하는 걸 다 해놓고 split함. 
        #(세현이 코드는 train,test 나눈 다음에 15일 -> 하루 예측하는걸 적용해서 test data 100->85개로 된 것.)
        
        for i in range(len(y) - window_size):
            _x = x[i:i + window_size]  # 이전 15일
            _y = y[i + window_size]  # 다음날 종가
            data_x.append(_x)
            data_y.append(_y)

        # Train dataset
        train_size = int(len(data_y) * 0.7)
        train_x = np.array(data_x[0:train_size])
        train_y = np.array(data_y[0:train_size])

        # Test dataset
        test_size = len(data_y) - train_size
        test_x = np.array(data_x[train_size:len(data_x)])
        test_y = np.array(data_y[train_size:len(data_y)])
        
        return train_x, train_y, test_x, test_y, dfy

#    def to_price():
#        total_data = len(test_y) #494
#        training_days = total_data - test_days
#        test_original = df_original.iloc[training_days:] 
#        pred_data = pd.DataFrame(predictions[:,0], test_original.index,columns=['predictions'])
#        return pred_data

    def LSTM_model(self, row):
        train_x, train_y, test_x, test_y, dfy = LSTM_Prediction.dataset(row)
        window_size = 15
        model = Sequential()
        model.add(LSTM(units=10, activation='relu', return_sequences=True, input_shape=(window_size, 5)))
        model.add(Dropout(0.1))
        model.add(LSTM(units=10, activation='relu'))
        model.add(Dropout(0.1))
        model.add(Dense(units=1))
#        model.summary()

        model.compile(optimizer='adam', loss='mean_squared_error')
        model.fit(train_x, train_y, epochs=20, batch_size=128)
        
        allpred_y = model.predict(test_x)
        pred_y = model.predict(test_x[len(test_y)-15:])

        if pred_y[0].item() == 0:
            final_return = 0
        else:
            final_return = (pred_y[-1].item() - pred_y[0].item()) / pred_y[0].item()
        
        
#        plt.figure()
#        plt.plot(test_y, color='red', label='real stock price')
#        plt.plot(allpred_y, color='blue', label='predicted stock price')
#        tmp = np.full((129,1),np.nan)
#        tmp = np.append(tmp,pred_y)
#        plt.plot(tmp, color='gold', label='predicted stock price 15 days')
#        plt.xlim(0,146)
#        plt.xlabel('time')
#        plt.legend()
#        plt.show()

        return final_return

In [46]:
#lstm_pred = LSTM_Prediction()
#pred_y = lstm_pred.LSTM_model(train)

# 적용

In [48]:
# 추론 결과를 저장하기 위한 dataframe 생성
results_df = pd.DataFrame(columns=['종목코드', 'final_return'])

# train 데이터에 존재하는 독립적인 종목코드 추출
unique_codes = train['종목코드'].unique()
lstm_pred = LSTM_Prediction()

# 각 종목코드에 대해서 모델 학습 및 추론 반복
for code in tqdm(unique_codes[:]):
    train_close = train[train['종목코드'] == code]
    final_return = lstm_pred.LSTM_model(train_close)

    # 결과 저장
    results_df = pd.concat([results_df, pd.DataFrame({'종목코드': [code], 'final_return': [final_return]})])

  0%|          | 0/2000 [00:00<?, ?it/s]

Epoch 1/20
3/3 [==============================] - 2s 11ms/step - loss: 0.3100
Epoch 2/20
3/3 [==============================] - 0s 10ms/step - loss: 0.2956
Epoch 3/20
3/3 [==============================] - 0s 10ms/step - loss: 0.2838
Epoch 4/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2723
Epoch 5/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2617
Epoch 6/20
3/3 [==============================] - 0s 10ms/step - loss: 0.2510
Epoch 7/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2433
Epoch 8/20
3/3 [==============================] - 0s 10ms/step - loss: 0.2355
Epoch 9/20
3/3 [==============================] - 0s 10ms/step - loss: 0.2269
Epoch 10/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2173
Epoch 11/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2049
Epoch 12/20
3/3 [==============================] - 0s 10ms/step - loss: 0.1870
Epoch 13/20
3/3 [==============================] - 0s 11ms/st

  0%|          | 1/2000 [00:03<1:56:26,  3.49s/it]

Epoch 1/20
3/3 [==============================] - 2s 11ms/step - loss: 0.2316
Epoch 2/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2094
Epoch 3/20
3/3 [==============================] - 0s 10ms/step - loss: 0.1936
Epoch 4/20
3/3 [==============================] - 0s 11ms/step - loss: 0.1777
Epoch 5/20
3/3 [==============================] - 0s 10ms/step - loss: 0.1601
Epoch 6/20
3/3 [==============================] - 0s 10ms/step - loss: 0.1352
Epoch 7/20
3/3 [==============================] - 0s 9ms/step - loss: 0.1175
Epoch 8/20
3/3 [==============================] - 0s 11ms/step - loss: 0.0949
Epoch 9/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0732
Epoch 10/20
3/3 [==============================] - 0s 11ms/step - loss: 0.0505
Epoch 11/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0295
Epoch 12/20
3/3 [==============================] - 0s 12ms/step - loss: 0.0214
Epoch 13/20
3/3 [==============================] - 0s 10ms/ste

  0%|          | 2/2000 [00:06<1:50:09,  3.31s/it]

...

100%|█████████▉| 1998/2000 [1:53:10<00:07,  3.86s/it]

Epoch 1/20
3/3 [==============================] - 2s 11ms/step - loss: 0.1119
Epoch 2/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0944
Epoch 3/20
3/3 [==============================] - 0s 11ms/step - loss: 0.0808
Epoch 4/20
3/3 [==============================] - 0s 11ms/step - loss: 0.0659
Epoch 5/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0547
Epoch 6/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0479
Epoch 7/20
3/3 [==============================] - 0s 11ms/step - loss: 0.0375
Epoch 8/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0290
Epoch 9/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0212
Epoch 10/20
3/3 [==============================] - 0s 10ms/step - loss: 0.0167
Epoch 11/20
3/3 [==============================] - 0s 11ms/step - loss: 0.0113
Epoch 12/20
3/3 [==============================] - 0s 11ms/step - loss: 0.0102
Epoch 13/20
3/3 [==============================] - 0s 11ms/st

100%|█████████▉| 1999/2000 [1:53:14<00:03,  3.63s/it]

Epoch 1/20
3/3 [==============================] - 2s 11ms/step - loss: 0.4942
Epoch 2/20
3/3 [==============================] - 0s 11ms/step - loss: 0.4557
Epoch 3/20
3/3 [==============================] - 0s 11ms/step - loss: 0.4130
Epoch 4/20
3/3 [==============================] - 0s 11ms/step - loss: 0.3825
Epoch 5/20
3/3 [==============================] - 0s 10ms/step - loss: 0.3557
Epoch 6/20
3/3 [==============================] - 0s 10ms/step - loss: 0.3332
Epoch 7/20
3/3 [==============================] - 0s 11ms/step - loss: 0.3151
Epoch 8/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2989
Epoch 9/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2870
Epoch 10/20
3/3 [==============================] - 0s 12ms/step - loss: 0.2743
Epoch 11/20
3/3 [==============================] - 0s 11ms/step - loss: 0.2645
Epoch 12/20
3/3 [==============================] - 0s 10ms/step - loss: 0.2562
Epoch 13/20
3/3 [==============================] - 0s 11ms/st

100%|██████████| 2000/2000 [1:53:17<00:00,  3.40s/it]


In [49]:
results_df

종목코드  final_return
0   A060310      0.006000
0   A095570     -0.144226
0   A006840     -0.026915
0   A054620     -0.058822
0   A265520      0.014144
..      ...           ...
0   A189980      0.406985
0   A000540      0.037392
0   A003280      0.001116
0   A037440     -0.008547
0   A238490     -0.003749

[2000 rows x 2 columns]

In [50]:
results_df_final = results_df.copy()

In [51]:
results_df_final.to_csv("submission_lstm_0729_withfinalreturn_ver2.csv")

In [52]:
results_df_final = results_df_final.fillna(0)

In [53]:
results_df_lstm = results_df_final.copy()

In [54]:
results_df_lstm['순위'] = results_df_lstm['final_return'].rank(method='first', ascending=False).astype('int') # 각 순위를 중복없이 생성

In [55]:
results_df_lstm = results_df_lstm.drop("final_return", axis=1)

In [57]:
results_df_lstm.to_csv("submission_lstm_0729_ver2.csv")

In [39]:
results_df_lstm

종목코드    순위
0   A339950  1312
0   A099190  1735
0   A289010  1301
0   A214430    73
0   A040910    79
..      ...   ...
0   A020560  1332
0   A143160  1578
0   A054800  1229
0   A332370  1411
0   A122900   825

[2000 rows x 2 columns]